In [50]:
from langchain_community.document_loaders import TextLoader # loading text files to a type that langchain can understand
from langchain_text_splitters import CharacterTextSplitter # splitting text into smaller chunks (description of each book)
from langchain_openai import OpenAIEmbeddings # converting documents into numerical representation (doc embeddings)
from langchain_chroma import Chroma # vector database to store and query embeddings

In [51]:
from dotenv import load_dotenv

load_dotenv()

True

In [52]:
import pandas as pd

books = pd.read_csv("books_cleaned.csv")

In [53]:
books.head()

isbn13      isbn10                title  \
0  9.780002e+12  0002005883               Gilead   
1  9.780002e+12  0002261987         Spider's Web   
2  9.780006e+12  0006178731       Rage of angels   
3  9.780006e+12  0006280897       The Four Loves   
4  9.780006e+12  0006280935  The Problem of Pain   

                           authors                     categories  \
0               Marilynne Robinson                        Fiction   
1  Charles Osborne;Agatha Christie  Detective and mystery stories   
2                   Sidney Sheldon                        Fiction   
3              Clive Staples Lewis                 Christian life   
4              Clive Staples Lewis                 Christian life   

                                           thumbnail  \
0  http://books.google.com/books/content?id=KQZCP...   
1  http://books.google.com/books/content?id=gA5GP...   
2  http://books.google.com/books/content?id=FKo2T...   
3  http://books.google.com/books/content?id=XhQ5X...   
4  http://books.google.com/books/content?id=Kk-uV...   

                                         description  published_year  \
0  A NOVEL THAT READERS and critics have been eag...          2004.0   
1  A new 'Christie for Christmas' -- a full-lengt...          2000.0   
2  A memorable, mesmerizing heroine Jennifer -- b...          1993.0   
3  Lewis' work on the nature of love divides love...          2002.0   
4  "In The Problem of Pain, C.S. Lewis, one of th...          2002.0   

   average_rating  num_pages  ratings_count     title_and_subtitle  \
0            3.85      247.0          361.0                 Gilead   
1            3.83      241.0         5164.0  Spider's Web: A Novel   
2            3.93      512.0        29532.0         Rage of angels   
3            4.15      170.0        33684.0         The Four Loves   
4            4.09      176.0        37569.0    The Problem of Pain   

                                  tagged_description  
0  9780002005883.0 A NOVEL THAT READERS and criti...  
1  9780002261982.0 A new 'Christie for Christmas'...  
2  9780006178736.0 A memorable, mesmerizing heroi...  
3  9780006280897.0 Lewis' work on the nature of l...  
4  9780006280934.0 "In The Problem of Pain, C.S. ...

In [54]:
books["tagged_description"]

0       9780002005883.0 A NOVEL THAT READERS and criti...
1       9780002261982.0 A new 'Christie for Christmas'...
2       9780006178736.0 A memorable, mesmerizing heroi...
3       9780006280897.0 Lewis' work on the nature of l...
4       9780006280934.0 "In The Problem of Pain, C.S. ...
                              ...                        
5192    9788172235222.0 On A Train Journey Home To Nor...
5193    9788173031014.0 This book tells the tale of a ...
5194    9788179921623.0 Wisdom to Create a Life of Pas...
5195    9788185300535.0 This collection of the timeles...
5196    9789027712059.0 Since the three volume edition...
Name: tagged_description, Length: 5197, dtype: object

In [55]:
books["tagged_description"].to_csv("tagged_description.txt",
                                   sep = "\n",
                                   index = False,
                                   header = False)

In [56]:
raw_documents = TextLoader("tagged_description.txt").load()
text_splitter = CharacterTextSplitter(chunk_size=10**9, chunk_overlap=0, separator="\n")
documents = text_splitter.split_documents(raw_documents)

In [57]:
print(documents[0])

page_content='9780002005883.0 A NOVEL THAT READERS and critics have been eagerly anticipating for over a decade, Gilead is an astonishingly imagined story of remarkable lives. John Ames is a preacher, the son of a preacher and the grandson (both maternal and paternal) of preachers. It’s 1956 in Gilead, Iowa, towards the end of the Reverend Ames’s life, and he is absorbed in recording his family’s story, a legacy for the young son he will never see grow up. Haunted by his grandfather’s presence, John tells of the rift between his grandfather and his father: the elder, an angry visionary who fought for the abolitionist cause, and his son, an ardent pacifist. He is troubled, too, by his prodigal namesake, Jack (John Ames) Boughton, his best friend’s lost son who returns to Gilead searching for forgiveness and redemption. Told in John Ames’s joyous, rambling voice that finds beauty, humour and truth in the smallest of life’s details, Gilead is a song of celebration and acceptance of the be

In [58]:
from langchain_community.embeddings import HuggingFaceBgeEmbeddings

In [59]:
# 3) Strong local embeddings (BGE-large)
embeddings = HuggingFaceBgeEmbeddings(
    model_name="BAAI/bge-large-en-v1.5",
    model_kwargs={"device": "cpu"},                  # set to "cuda" if you have a GPU
    encode_kwargs={"normalize_embeddings": True},    # recommended for cosine
)

In [66]:
import os
print(os.listdir("."))          # list current directory
print(os.path.abspath("chroma_db"))  # show full path to chroma_db

['books_cleaned.csv', 'books.csv', '.github', 'requirements.txt', '.git', 'data-exploration.ipynb', 'vector-search.ipynb', 'tagged_description.txt', '.env']
/home/dangvu/Desktop/book-recommendation/chroma_db


In [64]:
!rm -rf chroma_db

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [65]:
import shutil
shutil.rmtree("/home/dangvu/Desktop/book-recommendation/chroma_db", ignore_errors=True)

import os
print(os.path.exists("/home/dangvu/Desktop/book-recommendation/chroma_db"))  # should be False


False


In [72]:
db_books = Chroma.from_documents(
    documents,
    embedding=embeddings,
    collection_metadata={"hnsw:space": "cosine"},
    persist_directory="/home/dangvu/Desktop/book-recommendation/chroma_db"
)

In [73]:
query = "A book to teach children about nature"
docs = db_books.similarity_search(query, k = 10)
print(docs[0])

page_content='9780002005883.0 A NOVEL THAT READERS and critics have been eagerly anticipating for over a decade, Gilead is an astonishingly imagined story of remarkable lives. John Ames is a preacher, the son of a preacher and the grandson (both maternal and paternal) of preachers. It’s 1956 in Gilead, Iowa, towards the end of the Reverend Ames’s life, and he is absorbed in recording his family’s story, a legacy for the young son he will never see grow up. Haunted by his grandfather’s presence, John tells of the rift between his grandfather and his father: the elder, an angry visionary who fought for the abolitionist cause, and his son, an ardent pacifist. He is troubled, too, by his prodigal namesake, Jack (John Ames) Boughton, his best friend’s lost son who returns to Gilead searching for forgiveness and redemption. Told in John Ames’s joyous, rambling voice that finds beauty, humour and truth in the smallest of life’s details, Gilead is a song of celebration and acceptance of the be

In [80]:

def retrieve_semantic_recommendations(
        query: str,
        top_k: int = 10,
) -> pd.DataFrame:
    recs = db_books.similarity_search(query, k = 50)

    books_list = []

    for i in range(0, len(recs)):
        books_list += [float(recs[i].page_content.strip('\'"').split()[0])]

    return books[books["isbn13"].isin(books_list)]

In [81]:
retrieve_semantic_recommendations("A book to teach children about nature")

isbn13      isbn10   title             authors categories  \
0  9.780002e+12  0002005883  Gilead  Marilynne Robinson    Fiction   

                                           thumbnail  \
0  http://books.google.com/books/content?id=KQZCP...   

                                         description  published_year  \
0  A NOVEL THAT READERS and critics have been eag...          2004.0   

   average_rating  num_pages  ratings_count title_and_subtitle  \
0            3.85      247.0          361.0             Gilead   

                                  tagged_description  
0  9780002005883.0 A NOVEL THAT READERS and criti...